### Refresner

We get that first observation from the environment by calling env.reset()

Now, the agent has received the observation. It's time for the agent to take an action and send the action to the environment to see what happens. In essence, this is what the algorithms we develop for the agents should figure out.

Once the action to be taken is decided, we send it to the environment using the **env.step()**.

method, which will return four values in this order: **next_state, reward, done, and info.**

The next_state is the resulting state of the environment after the action was taken in the previous state.

The **reward** is returned by the environment.

The **done** variable is a Boolean (true or false), which gets a value of true if the episode has terminated/finished (therefore, it is time to reset the environment) and false otherwise. This will be useful for the agent to know when an episode has ended or when the environment is going to be reset to some initial state.

The info variable returned is an optional variable, which some environments may return with some additional information. Usually, this is not used by the agent to make its decision on which action to take.

## The Mountain Car problem and environment

In the Mountain Car Gym environment, a car is on a one-dimensional track, positioned between two mountains. The goal is to drive the car up the mountain on the right; however, the car's engine is not strong enough to drive up the mountain even at the maximum speed. Therefore, the only way to succeed is to drive back and forth to build up momentum. In short, the Mountain Car problem is to get an under-powered car to the top of a hill.

Before you implement your agent algorithm, it will help tremendously to understand the environment, the problem, and the state and action spaces. How do we find out the state and action spaces of the Mountain Car environment in the Gym? 

In [1]:
#!/usr/bin/env python
import gym
from gym.spaces import *
import sys

def print_spaces(space):
    print(space)
    if isinstance(space, Box): # Print lower and upper bound if it's a Box space
        print("\n space.low: ", space.low)
        print("\n space.high: ", space.high)

    
if __name__ == "__main__":
    env = gym.make('MountainCar-v0') # env = gym.make(sys.argv[1])
    print("Observation Space:")
    print_spaces(env.observation_space)
    print("Action Space:")
    print_spaces(env.action_space)
    try:
        print("Action description/meaning:",env.unwrapped.get_action_meanings())
    except AttributeError:
        pass

Observation Space:
Box(2,)

 space.low:  [-1.2  -0.07]

 space.high:  [0.6  0.07]
Action Space:
Discrete(3)


From this output, we can see that the state and observation space is a two-dimensional box and the action space is three-dimensional and discrete.

So for example, the car starts at a random position between -0.6 and -0.4 with zero velocity, and the goal is to reach the top of the hill on the right side, which is at position 0.5. (The car can technically go beyond 0.5, up to 0.6, which is also considered.) The environment will send -1 as a reward every time step until the goal position (0.5) is reached. The environment will terminate the episode. The done variable will be equal to True if the car reaches the 0.5 position or the number of steps taken reaches 200.

## Implementing a Q-learning agent

This will be our reinforcement learning Gym boiler plate code

MAX_NUM_EPISODES - This is the number of steps or actions that the agent can take before the episode ends.

This may be useful in continuing, perpetual, or looping environments, where the environment itself does not end the episode. Here, we set a limit for the agent to avoid infinite loops. However, most of the environments defined in OpenAI Gym have an episode termination condition and once either of them is satisfied.

The **done** variable returned by the env.step(...) function will be set to True, the environment will terminate the episode if the car reaches the goal position (0.5) or if the number of steps taken reaches 200. Therefore, we can further simplify the boilerplate code to look like the following for the Mountain Car environment:

In [7]:
#!/usr/bin/env python
import gym
env = gym.make("MountainCar-v0")
MAX_NUM_EPISODES = 10
STEPS_PER_EPISODE = 500

for episode in range(MAX_NUM_EPISODES):
    done = False
    obs = env.reset()
    total_reward = 0.0 # To keep track of the total reward obtained in each episode
    step = 0
    while not done:
        env.render()
        action = env.action_space.sample()# Sample random action. This will be replaced by our agent's action when we start developing the agent algorithms
        next_state, reward, done, info = env.step(action) # Send the action to the environment and receive the next_state, reward and whether done or not
        total_reward += reward
        step += 1
        obs = next_state

    print("\n Episode #{} ended in {} steps. total_reward={}".format(episode, step+1, total_reward))
env.close()


 Episode #0 ended in 201 steps. total_reward=-200.0

 Episode #1 ended in 201 steps. total_reward=-200.0

 Episode #2 ended in 201 steps. total_reward=-200.0

 Episode #3 ended in 201 steps. total_reward=-200.0

 Episode #4 ended in 201 steps. total_reward=-200.0

 Episode #5 ended in 201 steps. total_reward=-200.0

 Episode #6 ended in 201 steps. total_reward=-200.0

 Episode #7 ended in 201 steps. total_reward=-200.0

 Episode #8 ended in 201 steps. total_reward=-200.0

 Episode #9 ended in 201 steps. total_reward=-200.0


As you can see, the agent gets a reward of -1 for each step and that the MountainCar-v0 environment will terminate the episode after 200 steps; this is why you the agent may sometimes get a total reward of -200! After all.

The agent is taking random actions without thinking or learning from its previous actions. Ideally, we would want the agent to figure out how to reach the top of the mountain (near the flag, close to, at, or beyond position 0.5) with the minimum number of steps. 

Don't worry - we will build such an intelligent agent by the end of this chapter!

## Implementing a  Q-learning Agent

We will implement a Q_Learner **class**.

These will be the main methods:

__init__(self, env)

discretize(self, obs)

get_action(self, obs)

learn(self, obs, action, reward, next_obs)

You will later find that these methods are common and exist in almost all the agents.


The discretize() function is not necessary for agent implementations in general, but when the state space is large and continuous, it may be better to discretize the space into countable bins or ranges of values to simplify the representation. This also reduces the number of values that the Q-learning algorithm needs to learn, as it now only has to learn a finite set of values, which can be concisely represented in tabular formats or by using n-dimensional arrays instead of complex functions. Moreover, the Q-learning algorithm, used for optimal control, is guaranteed to converge for tabular representations of Q-values.

### Let make some definitions:

**EPSILON_MIN:** This is the minimum value of the epsilon value that we want the agent to use while following an epsilon-greedy policy.

**MAX_NUM_EPISODES:** The maximum number of episodes that we want the agent to interact with the environment for.

**STEPS_PER_EPISODE:** This is the number of steps in each episode. This could be the maximum number of steps that an environment will allow per episode or a custom value that we want to limit based on some time budget. Allowing a higher number of steps per episode means each episode might take longer to complete and in non-terminating environments, the environment won't be reset until this limit is reached, even if the agent is stuck at the same spot.

**ALPHA:** This is the learning rate that we want the agent to use. This is the alpha in the Q-learning update equation listed in the previous section. Some algorithms vary the learning rate as the training progresses.

**GAMMA:** This is the discount factor that the agent will use to factor in future rewards. This value corresponds to the gamma in the Q-learning update equation in the previous section.

**NUM_DISCRETE_BINS:** This is the number of bins of values that the state space will be discretized into. For the Mountain Car environment, we will be discretizing the state space into 30 bins. You can play around with higher/lower values.

In [8]:
EPSILON_MIN = 0.005
max_num_steps = MAX_NUM_EPISODES * STEPS_PER_EPISODE
EPSILON_DECAY = 500 * EPSILON_MIN / max_num_steps
ALPHA = 0.05  # Learning rate
GAMMA = 0.98  # Discount factor
NUM_DISCRETE_BINS = 30  # Number of bins to Discretize each observation dim

The Q_Learner class's member function definitions. 

The __init__(self, env) function takes the environment instance, env, as an input argument and initializes the dimensions/shape of the **observation space** and the **action space**, and also determines the parameters to discretize the observation space based on. 

The NUM_DISCRETE_BINS we set. The __init__(self, env) function also initializes the Q function as a NumPy array, based on the shape of the discretized observation space and the action space dimensions. 

The implementation of __init__(self, env) is straightforward as we are only initializing the necessary values for the agent.

In [10]:
EPSILON_MIN = 0.005
max_num_steps = MAX_NUM_EPISODES * STEPS_PER_EPISODE
EPSILON_DECAY = 500 * EPSILON_MIN / max_num_steps
ALPHA = 0.05  # Learning rate
GAMMA = 0.98  # Discount factor
NUM_DISCRETE_BINS = 30  # Number of bins to Discretize each observation dim

class Q_Learner(object):
    def __init__(self, env):
        self.obs_shape = env.observation_space.shape
        self.obs_high = env.observation_space.high
        self.obs_low = env.observation_space.low
        self.obs_bins = NUM_DISCRETE_BINS  # Number of bins to Discretize each observation dim
        self.bin_width = (self.obs_high - self.obs_low) / self.obs_bins
        self.action_shape = env.action_space.n
        # Create a multi-dimensional array (aka. Table) to represent the
        # Q-values
        self.Q = np.zeros((self.obs_bins + 1, self.obs_bins + 1,
                           self.action_shape))  # (51 x 51 x 3)
        self.alpha = ALPHA  # Learning rate
        self.gamma = GAMMA  # Discount factor
        self.epsilon = 1.0

    def discretize(self, obs):
        return tuple(((obs - self.obs_low) / self.bin_width).astype(int))

    def get_action(self, obs):
        discretized_obs = self.discretize(obs)
        # Epsilon-Greedy action selection
        if self.epsilon > EPSILON_MIN:
            self.epsilon -= EPSILON_DECAY
        if np.random.random() > self.epsilon:
            return np.argmax(self.Q[discretized_obs])
        else:  # Choose a random action
            return np.random.choice([a for a in range(self.action_shape)])

    def learn(self, obs, action, reward, next_obs):
        discretized_obs = self.discretize(obs)
        discretized_next_obs = self.discretize(next_obs)
        td_target = reward + self.gamma * np.max(self.Q[discretized_next_obs])
        td_error = td_target - self.Q[discretized_obs][action]
        self.Q[discretized_obs][action] += self.alpha * td_error
        

### The Q_learner class's learn method

As you might have guessed, this is the most important method of the Q_Learner class, which does the magic of learning the Q-values, which in turn enables the agent to take intelligent actions over time! 

The best part is that it is not that complicated to implement! It is merely the implementation of the Q-learning update equation.

In [2]:
 def learn(self, env, action, reward, next_env):
        discretized_env = self.discretize(env)
        discretized_next_obs = self.discretize(next_env)
        td_target = reward + self.gamma * np.max(self.Q[discretized_next_env])
        td_error = td_target - self.Q[discretized_env][action]
        self.Q[discretized_env][action] += self.alpha * td_error
        
# which is the same as 
#self.Q[discretized_env][action] += self.alpha * (reward + self.gamma * np.max(self.Q[discretized_next_env] - 
#                                                                              self.Q[discretized_env][action]

### Training the reinforcement learning Agent

The procedure to train the Q-learning agent may look familiar to you already, because it has many of the same lines of code as, and also a similar structure to, the boilerplate code that we used before. 

Instead of choosing a random action from the environment's actions space, we now get the action from the agent using the **agent.get_action(env)** method. We also call the **agent.learn(obs, action, reward, next_env)** method after sending the agent's action to the environment and receiving the feedback. The training function is listed here:

In [12]:
def train(agent, env):
    best_reward = -float('inf')
    for episode in range(MAX_NUM_EPISODES):
        done = False
        obs = env.reset()
        total_reward = 0.0
        while not done:
            action = agent.get_action(obs)
            next_obs, reward, done, info = env.step(action)
            agent.learn(obs, action, reward, next_obs)
            obs = next_obs
            total_reward += reward
        if total_reward > best_reward:
            best_reward = total_reward
        print("Episode#:{} reward:{} best_reward:{} eps:{}".format(episode,
                                     total_reward, best_reward, agent.epsilon))
    # Return the trained policy
    return np.argmax(agent.Q, axis=2)

## Complete Q-Learner implementation for the Mountain Car problem

In [14]:
#!/usr/bin/env/ python
import gym
import numpy as np

MAX_NUM_EPISODES = 50000
STEPS_PER_EPISODE = 200 #  This is specific to MountainCar. May change with env
EPSILON_MIN = 0.005
max_num_steps = MAX_NUM_EPISODES * STEPS_PER_EPISODE
EPSILON_DECAY = 500 * EPSILON_MIN / max_num_steps
ALPHA = 0.05  # Learning rate
GAMMA = 0.98  # Discount factor
NUM_DISCRETE_BINS = 30  # Number of bins to Discretize each observation dim

class Q_Learner(object):
    def __init__(self, env):
        self.obs_shape = env.observation_space.shape
        self.obs_high = env.observation_space.high
        self.obs_low = env.observation_space.low
        self.obs_bins = NUM_DISCRETE_BINS  # Number of bins to Discretize each observation dim
        self.bin_width = (self.obs_high - self.obs_low) / self.obs_bins
        self.action_shape = env.action_space.n
        # Create a multi-dimensional array (aka. Table) to represent the
        # Q-values
        self.Q = np.zeros((self.obs_bins + 1, self.obs_bins + 1,
                           self.action_shape))  # (51 x 51 x 3)
        self.alpha = ALPHA  # Learning rate
        self.gamma = GAMMA  # Discount factor
        self.epsilon = 1.0

    def discretize(self, obs):
        return tuple(((obs - self.obs_low) / self.bin_width).astype(int))

    def get_action(self, obs):
        discretized_obs = self.discretize(obs)
        # Epsilon-Greedy action selection
        if self.epsilon > EPSILON_MIN:
            self.epsilon -= EPSILON_DECAY
        if np.random.random() > self.epsilon:
            return np.argmax(self.Q[discretized_obs])
        else:  # Choose a random action
            return np.random.choice([a for a in range(self.action_shape)])

    def learn(self, obs, action, reward, next_obs):
        discretized_obs = self.discretize(obs)
        discretized_next_obs = self.discretize(next_obs)
        td_target = reward + self.gamma * np.max(self.Q[discretized_next_obs])
        td_error = td_target - self.Q[discretized_obs][action]
        self.Q[discretized_obs][action] += self.alpha * td_error

def train(agent, env):
    best_reward = -float('inf')
    for episode in range(MAX_NUM_EPISODES):
        done = False
        obs = env.reset()
        total_reward = 0.0
        while not done:
            action = agent.get_action(obs)
            next_obs, reward, done, info = env.step(action)
            agent.learn(obs, action, reward, next_obs)
            obs = next_obs
            total_reward += reward
        if total_reward > best_reward:
            best_reward = total_reward
        print("Episode#:{} reward:{} best_reward:{} eps:{}".format(episode,
                                     total_reward, best_reward, agent.epsilon))
    # Return the trained policy
    return np.argmax(agent.Q, axis=2)

def test(agent, env, policy):
    done = False
    obs = env.reset()
    total_reward = 0.0
    while not done:
        action = policy[agent.discretize(obs)]
        next_obs, reward, done, info = env.step(action)
        obs = next_obs
        total_reward += reward
    return total_reward

if __name__ == "__main__":
    env = gym.make('MountainCar-v0')
    agent = Q_Learner(env)
    learned_policy = train(agent, env)
    # Use the Gym Monitor wrapper to evalaute the agent and record video
    gym_monitor_path = "./gym_monitor_output"
    env = gym.wrappers.Monitor(env, gym_monitor_path, force=True)
    for _ in range(1000):
        test(agent, env, learned_policy)
    env.close()

Episode#:0 reward:-200.0 best_reward:-200.0 eps:0.999949999999993
Episode#:1 reward:-200.0 best_reward:-200.0 eps:0.999899999999986
Episode#:2 reward:-200.0 best_reward:-200.0 eps:0.999849999999979
Episode#:3 reward:-200.0 best_reward:-200.0 eps:0.999799999999972
Episode#:4 reward:-200.0 best_reward:-200.0 eps:0.999749999999965
Episode#:5 reward:-200.0 best_reward:-200.0 eps:0.9996999999999581
Episode#:6 reward:-200.0 best_reward:-200.0 eps:0.9996499999999511
Episode#:7 reward:-200.0 best_reward:-200.0 eps:0.9995999999999441
Episode#:8 reward:-200.0 best_reward:-200.0 eps:0.9995499999999371
Episode#:9 reward:-200.0 best_reward:-200.0 eps:0.9994999999999301
Episode#:10 reward:-200.0 best_reward:-200.0 eps:0.9994499999999231
Episode#:11 reward:-200.0 best_reward:-200.0 eps:0.9993999999999161
Episode#:12 reward:-200.0 best_reward:-200.0 eps:0.9993499999999091
Episode#:13 reward:-200.0 best_reward:-200.0 eps:0.9992999999999022
Episode#:14 reward:-200.0 best_reward:-200.0 eps:0.999249999999

Episode#:128 reward:-200.0 best_reward:-200.0 eps:0.9935499999990984
Episode#:129 reward:-200.0 best_reward:-200.0 eps:0.9934999999990914
Episode#:130 reward:-200.0 best_reward:-200.0 eps:0.9934499999990845
Episode#:131 reward:-200.0 best_reward:-200.0 eps:0.9933999999990775
Episode#:132 reward:-200.0 best_reward:-200.0 eps:0.9933499999990705
Episode#:133 reward:-200.0 best_reward:-200.0 eps:0.9932999999990635
Episode#:134 reward:-200.0 best_reward:-200.0 eps:0.9932499999990565
Episode#:135 reward:-200.0 best_reward:-200.0 eps:0.9931999999990495
Episode#:136 reward:-200.0 best_reward:-200.0 eps:0.9931499999990425
Episode#:137 reward:-200.0 best_reward:-200.0 eps:0.9930999999990355
Episode#:138 reward:-200.0 best_reward:-200.0 eps:0.9930499999990285
Episode#:139 reward:-200.0 best_reward:-200.0 eps:0.9929999999990216
Episode#:140 reward:-200.0 best_reward:-200.0 eps:0.9929499999990146
Episode#:141 reward:-200.0 best_reward:-200.0 eps:0.9928999999990076
Episode#:142 reward:-200.0 best_re

Episode#:258 reward:-200.0 best_reward:-200.0 eps:0.9870499999981899
Episode#:259 reward:-200.0 best_reward:-200.0 eps:0.9869999999981829
Episode#:260 reward:-200.0 best_reward:-200.0 eps:0.9869499999981759
Episode#:261 reward:-200.0 best_reward:-200.0 eps:0.9868999999981689
Episode#:262 reward:-200.0 best_reward:-200.0 eps:0.9868499999981619
Episode#:263 reward:-200.0 best_reward:-200.0 eps:0.9867999999981549
Episode#:264 reward:-200.0 best_reward:-200.0 eps:0.9867499999981479
Episode#:265 reward:-200.0 best_reward:-200.0 eps:0.986699999998141
Episode#:266 reward:-200.0 best_reward:-200.0 eps:0.986649999998134
Episode#:267 reward:-200.0 best_reward:-200.0 eps:0.986599999998127
Episode#:268 reward:-200.0 best_reward:-200.0 eps:0.98654999999812
Episode#:269 reward:-200.0 best_reward:-200.0 eps:0.986499999998113
Episode#:270 reward:-200.0 best_reward:-200.0 eps:0.986449999998106
Episode#:271 reward:-200.0 best_reward:-200.0 eps:0.986399999998099
Episode#:272 reward:-200.0 best_reward:-20

Episode#:391 reward:-200.0 best_reward:-200.0 eps:0.9803999999972604
Episode#:392 reward:-200.0 best_reward:-200.0 eps:0.9803499999972534
Episode#:393 reward:-200.0 best_reward:-200.0 eps:0.9802999999972464
Episode#:394 reward:-200.0 best_reward:-200.0 eps:0.9802499999972394
Episode#:395 reward:-200.0 best_reward:-200.0 eps:0.9801999999972324
Episode#:396 reward:-200.0 best_reward:-200.0 eps:0.9801499999972254
Episode#:397 reward:-200.0 best_reward:-200.0 eps:0.9800999999972184
Episode#:398 reward:-200.0 best_reward:-200.0 eps:0.9800499999972114
Episode#:399 reward:-200.0 best_reward:-200.0 eps:0.9799999999972044
Episode#:400 reward:-200.0 best_reward:-200.0 eps:0.9799499999971975
Episode#:401 reward:-200.0 best_reward:-200.0 eps:0.9798999999971905
Episode#:402 reward:-200.0 best_reward:-200.0 eps:0.9798499999971835
Episode#:403 reward:-200.0 best_reward:-200.0 eps:0.9797999999971765
Episode#:404 reward:-200.0 best_reward:-200.0 eps:0.9797499999971695
Episode#:405 reward:-200.0 best_re

Episode#:510 reward:-200.0 best_reward:-200.0 eps:0.9744499999964287
Episode#:511 reward:-200.0 best_reward:-200.0 eps:0.9743999999964217
Episode#:512 reward:-200.0 best_reward:-200.0 eps:0.9743499999964147
Episode#:513 reward:-200.0 best_reward:-200.0 eps:0.9742999999964077
Episode#:514 reward:-200.0 best_reward:-200.0 eps:0.9742499999964007
Episode#:515 reward:-200.0 best_reward:-200.0 eps:0.9741999999963937
Episode#:516 reward:-200.0 best_reward:-200.0 eps:0.9741499999963867
Episode#:517 reward:-200.0 best_reward:-200.0 eps:0.9740999999963798
Episode#:518 reward:-200.0 best_reward:-200.0 eps:0.9740499999963728
Episode#:519 reward:-200.0 best_reward:-200.0 eps:0.9739999999963658
Episode#:520 reward:-200.0 best_reward:-200.0 eps:0.9739499999963588
Episode#:521 reward:-200.0 best_reward:-200.0 eps:0.9738999999963518
Episode#:522 reward:-200.0 best_reward:-200.0 eps:0.9738499999963448
Episode#:523 reward:-200.0 best_reward:-200.0 eps:0.9737999999963378
Episode#:524 reward:-200.0 best_re

...

Episode#:49510 reward:-118.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49511 reward:-153.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49512 reward:-118.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49513 reward:-133.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49514 reward:-117.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49515 reward:-143.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49516 reward:-125.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49517 reward:-144.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49518 reward:-151.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49519 reward:-124.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49520 reward:-146.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49521 reward:-120.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49522 reward:-147.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49523 reward:-116.0 best_reward:-86.0 eps:

Episode#:49631 reward:-118.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49632 reward:-150.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49633 reward:-124.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49634 reward:-150.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49635 reward:-145.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49636 reward:-115.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49637 reward:-119.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49638 reward:-145.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49639 reward:-121.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49640 reward:-117.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49641 reward:-153.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49642 reward:-146.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49643 reward:-150.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49644 reward:-147.0 best_reward:-86.0 eps:

Episode#:49749 reward:-147.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49750 reward:-123.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49751 reward:-143.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49752 reward:-118.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49753 reward:-147.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49754 reward:-149.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49755 reward:-145.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49756 reward:-116.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49757 reward:-144.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49758 reward:-119.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49759 reward:-144.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49760 reward:-145.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49761 reward:-145.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49762 reward:-126.0 best_reward:-86.0 eps:

Episode#:49869 reward:-147.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49870 reward:-153.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49871 reward:-146.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49872 reward:-150.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49873 reward:-154.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49874 reward:-146.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49875 reward:-142.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49876 reward:-144.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49877 reward:-147.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49878 reward:-144.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49879 reward:-122.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49880 reward:-127.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49881 reward:-150.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49882 reward:-123.0 best_reward:-86.0 eps:

Episode#:49988 reward:-151.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49989 reward:-122.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49990 reward:-149.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49991 reward:-152.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49992 reward:-123.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49993 reward:-146.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49994 reward:-120.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49995 reward:-116.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49996 reward:-151.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49997 reward:-116.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49998 reward:-124.0 best_reward:-86.0 eps:0.0049999999486979654
Episode#:49999 reward:-125.0 best_reward:-86.0 eps:0.0049999999486979654


Once the script finishes running, it it stores videos on the **'./gym_monitor_output'** directory and  see the recorded videos (along with some .stats.json and .meta.json files) of the agent's performance in the gym_monitor_output folder. You can watch the videos to see how your agent performed!


## Summary

We implemented an agent that learned to solve the Mountain Car problem smartly in 7 minutes or so!

We started by understanding the famous Mountain Car problem and looking at how the environment, the observation space, the state space, and rewards are designed in the Gym's MountainCar-v0 environment. We revisited the reinforcement learning Gym boilerplate.

We then defined the hyperparameters for our Q-learning agent and started implementing a Q-learning algorithm from scratch. 

We first implemented the agent's initialization function to initialize the agent's internal state variables, including the Q value representation, using a NumPy n-dimensional array. 

Then, we implemented the discretize method to discretize the state space; the get_action(...) method to select an action based on an epsilon-greedy policy; and then finally the learn(...) function, which implements the Q-learning update rule and forms the core of the agent. 

We saw how simple it was to implement them all! We also implemented functions to train, test, and evaluate the agent's performance. 

I hope you had a lot of fun implementing the agent and watching it solve the Mountain Car problem at the Gym! 